In [ ]:
import re
import csv
import pandas
import sqlite3
import random
import json
import itertools
import numpy as np
from sumeval.metrics.rouge import RougeCalculator
rouge = RougeCalculator(stopwords=False, lang="en")

from utils import *

In [ ]:
db_file = 'mimic_db/mimic.db'
model = query(db_file)
(db_meta, db_tabs, db_head) = model._load_db(db_file)

In [ ]:
fp = open('mimic_db/lookup.json', 'r')
lookup = json.load(fp)
fp.close()

In [ ]:
headerDic = []
for tb in lookup:
    for hd in lookup[tb]:
        headerDic.append('.'.join([tb,hd]).lower())
# print(headerDic)

In [ ]:
fp = open('generated_sql/output.json', 'r')
cnt = 0
sql_rec = []
for line in fp:
    line = json.loads(line)
    pred = re.split('<stop>', line['sql_pred'])[0]
    ttt = line['sql_gold']

#     print(pred)
    predArr = re.split("where", pred)
    predAgg = re.split("\s", predArr[0])
    predAgg = list(filter(None, predAgg))
    predAgg2 = []
    for k in range(len(predAgg)-1):
        if predAgg[k] in headerDic and predAgg[k+1] in headerDic:
            predAgg2.append(predAgg[k] + ',')
        else:
            predAgg2.append(predAgg[k])
    predAgg2.append(predAgg[-1])
    predAgg = ' '.join(predAgg2)
    
    predCon = re.split("and", predArr[1])
    predConNew = []
    k = 0
    while k < len(predCon):
        if "=" in predCon[k] or "<" in predCon[k] or ">" in predCon[k]:
            predConNew.append(predCon[k])
        else:
            predConNew[-1] += " and " + predCon[k]
            k += 1
        k += 1
    for k in range(len(predConNew)):
        if "=" in predConNew[k]:
            conOp = "="
        if ">" in predConNew[k]:
            conOp = ">"
        if "<" in predConNew[k]:
            conOp = "<"
        if "<=" in predConNew[k]:
            conOp = "<="
        if ">=" in predConNew[k]:
            conOp = ">="
        conVal = re.split("=|<|>", predConNew[k])
        conVal = list(filter(None, conVal))
        conCol = conVal[0]
        conColArr = re.split('\.|\s', conCol)
        conColArr = list(filter(None, conColArr))
        try:
            pool_ = lookup[conColArr[0].upper()][conColArr[1].upper()]
        except:
            sql_rec.append(["Error", ttt])
            continue
        conVal = re.split('"|\s', conVal[-1])
        conVal = list(filter(None, conVal))
        conVal = ' '.join(conVal)
        predConNew[k] = conCol + conOp + ' "' + conVal + '"'

    pred = predAgg + ' where ' + ' and '.join(predConNew)
    pred = re.split("\s", pred)
    pred = list(filter(None, pred))
    pred = " ".join(pred)
#     print(pred)
#     print(ttt)
#     print()
    sql_rec.append([pred, ttt])
    try:
        myres = model.execute_sql(pred).fetchall()
        myres = list({k[0]: {} for k in myres if not k[0] == None})
        cnt += 1
    except:
        pass
    
fp.close()
print(cnt)

## Logic Form Accuracy:

In [ ]:
cnt = 0
for itm in sql_rec:
    arr = re.split(',|\s', itm[0].lower())
    arr = list(filter(None, arr))
    arr = ' '.join(arr)
    if arr == itm[1]:
        cnt += 1
print('Logic Form Accuracy: {}'.format(cnt/1000))

In [ ]:
fp = open('generated_sql/output.json', 'r')
cnt = 0
lblb = 0
sql_rec2 = []
for line in fp:
    line = json.loads(line)
    pred = re.split('<stop>', line['sql_pred'])[0]
    ttt = line['sql_gold']

#     print(pred)
    predArr = re.split("where", pred)
    predAgg = re.split("\s", predArr[0])
    predAgg = list(filter(None, predAgg))
    predAgg2 = []
    for k in range(len(predAgg)-1):
        if predAgg[k] in headerDic and predAgg[k+1] in headerDic:
            predAgg2.append(predAgg[k] + ',')
        else:
            predAgg2.append(predAgg[k])
    predAgg2.append(predAgg[-1])
    predAgg = ' '.join(predAgg2)
    
    predCon = re.split("and", predArr[1])
    predConNew = []
    k = 0
    while k < len(predCon):
        if "=" in predCon[k] or "<" in predCon[k] or ">" in predCon[k]:
            predConNew.append(predCon[k])
        else:
            predConNew[-1] += " and " + predCon[k]
            k += 1
        k += 1
    for k in range(len(predConNew)):
        if "=" in predConNew[k]:
            conOp = "="
        if ">" in predConNew[k]:
            conOp = ">"
        if "<" in predConNew[k]:
            conOp = "<"
        if "<=" in predConNew[k]:
            conOp = "<="
        if ">=" in predConNew[k]:
            conOp = ">="
        conVal = re.split("=|<|>", predConNew[k])
        conVal = list(filter(None, conVal))
        conCol = conVal[0]
        conColArr = re.split('\.|\s', conCol)
        conColArr = list(filter(None, conColArr))
        try:
            pool_ = lookup[conColArr[0].upper()][conColArr[1].upper()]
        except:
            sql_rec2.append(["Error", ttt])
            lblb = 1
            break
        conVal = re.split('"|\s', conVal[-1])
        conVal = list(filter(None, conVal))
        conVal = ' '.join(conVal)
        try:
            int(conVal)
            predConNew[k] = conCol + conOp + ' "' + conVal + '"'
        except:
            predConNew[k] = 'lower(' + conCol + ')' + conOp + ' "' + conVal + '"'
    
    if lblb ==1:
        lblb = 0
        continue
    pred = predAgg + ' where ' + ' and '.join(predConNew)
    pred = re.split("\s", pred)
    pred = list(filter(None, pred))
    pred = " ".join(pred)
#     print(pred)
#     print(ttt)
#     print()
    sql_rec2.append([pred, ttt])
    try:
        myres = model.execute_sql(pred).fetchall()
        myres = list({k[0]: {} for k in myres if not k[0] == None})
        cnt += 1
    except:
        pass
    
fp.close()
print(cnt)

In [ ]:
fp = open("../mimicsql_data/mimicsql_natural/test.json", 'r')
cnt = 0
for line in fp:
    data = json.loads(line)
    sql_rec2[cnt][1] = data['sql']
    cnt += 1
fp.close()
print(cnt)

## Execution Accuracy:

In [ ]:
cnt = 0
k = 0
for itm in sql_rec2:
    [pred, ttt] = itm
    try:
        outPred = model.execute_sql(pred).fetchall()
        outTtt = model.execute_sql(ttt).fetchall()
    except:
        k += 1
        continue
    if outPred == outTtt:
        cnt += 1
#     else:
#         if sql_rec[k][0] == sql_rec[k][1].lower():
#             print(pred)
#             print(sql_rec[k][0])
#             print(ttt.lower())
#             print(ttt)
#             print(outPred)
#             print(outTtt)
#             print()
    k += 1
print('Execution Accuracy: {}'.format(cnt/1000))